In [138]:
from io import StringIO
import os
import itertools
import pickle
import time
from bs4 import BeautifulSoup
from tika import parser
import pandas as pd
from collections import Counter
import re
#import camelot
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [139]:
file = 'F://Environmental Baseline Data//Version 4 - Final//Indices/Index 2 - PDFs for Major Projects with ESAs.xlsx'

index2 = pd.read_excel(file, sheet_name="Sheet1")
index2.head()

file_name  \
0          A0H8C0 - 13.0 EIA - Section 13.1 to 13.6    
1   A0H8C1 - 13.0 EIA - Section 13.7 Wildlife Part 1   
2  A0H8C2 - 13.0 EIA - Section 13.7 Wildlife Part 2    
3          A0H8C3 - 13.0 EIA - Section 13.8 to 13.13   
4           A0H8C4 - 13.1 App 13A - Alignment Sheets   

                                    application_name  \
0  2003-03-17 Application to Construct and Operat...   
1  2003-03-17 Application to Construct and Operat...   
2  2003-03-17 Application to Construct and Operat...   
3  2003-03-17 Application to Construct and Operat...   
4  2003-03-17 Application to Construct and Operat...   

                                     esa_folder_link DocumentID  DataID  \
0  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A0H8C0  268706   
1  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A0H8C1  268709   
2  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A0H8C2  268712   
3  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A0H8C3  269018   
4  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A0H8C4  269021   

                                   esa_download_link  DataID_pdf  Section  \
0  https://apps.cer-rec.gc.ca/REGDOCS/File/Downlo...  268706.pdf       52   
1  https://apps.cer-rec.gc.ca/REGDOCS/File/Downlo...  268709.pdf       52   
2  https://apps.cer-rec.gc.ca/REGDOCS/File/Downlo...  268712.pdf       52   
3  https://apps.cer-rec.gc.ca/REGDOCS/File/Downlo...  269018.pdf       52   
4  https://apps.cer-rec.gc.ca/REGDOCS/File/Downlo...  269021.pdf       52   

  Application filing date                            link to folder with ESA  \
0              2003-03-17  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   
1              2003-03-17  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   
2              2003-03-17  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   
3              2003-03-17  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   
4              2003-03-17  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   

   ...                                Link to Application  \
0  ...  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   
1  ...  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   
2  ...  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   
3  ...  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   
4  ...  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...   

                                    Link to Decision Location_x   Component  \
0  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...        TBD         ESA   
1  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...        TBD         ESA   
2  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...        TBD         ESA   
3  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...        TBD         ESA   
4  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/2...        TBD  Appendices   

                                  Component PDF Name Component Index  \
0  Section 13.1: Introduction, Section 13.1: Proj...             1.0   
1        Section 13.7: Wildlife and Wildlife Habitat             2.0   
2        Section 13.7: Wildlife and Wildlife Habitat             3.0   
3  Section 13.8: Fisheries and Aquatic Resources,...             4.0   
4       Appendix 13A: Environmental Alignment Sheets             5.0   

  table_count short_name                 Location_y Commodity  
0        42.0      Ekwan  Alberta, British Columbia       Gas  
1        15.0      Ekwan  Alberta, British Columbia       Gas  
2        17.0      Ekwan  Alberta, British Columbia       Gas  
3         9.0      Ekwan  Alberta, British Columbia       Gas  
4         NaN      Ekwan  Alberta, British Columbia       Gas  

[5 rows x 29 columns]

In [115]:
path = 'F:/Environmental Baseline Data/Version 4 - Final/Pickles/'
paths = os.listdir(path)
all_paths = [path + str(x) for x in paths]
len(all_paths)
#all_paths = all_paths[:10]
     
a_paths = []
for paths in all_paths:
    if '1059872' in paths:
        a_paths.append(paths)    

        
#all_paths = a_paths

1902

In [116]:
#LABEL_HEADINGS =        ('plate', 'figure', 'photo', 'image', 'table', 'appendix')
#LABEL_HEADINGS_PLURAL = ('plates', 'figures', 'photos', 'images', 'tables', 'appendices')
searchlist = ['Image', 'Figure', 'Photo']
searchfor = []
for search in searchlist:
    searchfor.append(search)
    searchfor.append(search + 's')
    searchfor.append(search.upper())
    searchfor.append(search.upper() + 'S')
set(searchfor)

{'FIGURE',
 'FIGURES',
 'Figure',
 'Figures',
 'IMAGE',
 'IMAGES',
 'Image',
 'Images',
 'PHOTO',
 'PHOTOS',
 'Photo',
 'Photos'}

In [117]:
#open pickle file to extact strings startswith figure or title
#7 min execution time

start = time.time()
file_name = []
page_number = []
table_title = []
table_title_next = []

exceptions_list = ['...', 'Table of Content', 'TABLE OF CONTENTS', 'Table des matières', 'TABLE DES MATIÈRES'] 
last_ptag_starts_with_key = 0
for x in all_paths:
    with open(x, 'rb') as f:
        data = pickle.load(f)
        soup = BeautifulSoup(data['content'], 'lxml')
        pages = soup.find_all('div', attrs={'class': 'page'})
        for b, p in enumerate(pages):
            pages_text = [x.text for x in p.find_all('p')]
            for y in pages_text:
                if last_ptag_starts_with_key ==1:
                    table_title_next.append(y.replace('\n',' ').replace('\r',''))
                last_ptag_starts_with_key = 0
                
                ytest = y.replace('\n','').replace('\r','')
                ytest = ytest.split(" ")
                ytest_no_blanks = ""
                for ytes in ytest:
                    if len(ytes) > 2:
                        ytest_no_blanks = ytest_no_blanks + ytes + " "
                        
                if ytest_no_blanks.startswith(('Table', 'TABLE', 'FIGURE', 'FIGURES', 'Figure', 'Figures', 'IMAGE', 'IMAGES', 
                                               'Image', 'Images', 'PHOTO', 'PHOTOS', 'Photo', 
                                               'Photos')) and not any(substring in y for substring in exceptions_list):
                    file_name.append(x)
                    table_title.append(y.replace('\n','').replace('\r',''))
                    page_number.append(b + 1)
                    last_ptag_starts_with_key = 1
#                   
print('Time: ', time.time() - start)

Time:  281.28508734703064


In [140]:
len(file_name)
len(table_title)
len(page_number)
len(table_title_next)

39989

39989

39989

39989

# Categorization Function 

Here we are trying to categorize the potential table/figure titles (p-tags starting with the keywords Figues, Tables, etc.) extracted by the TIKA package into Table titles and sentences. The correct table titles extracted will allow us to correctly get the table titles for the tables extracted by Camelot package. <br>


The categorization of these potential table/figure titles is dones in the following manner: <br>
0 -> Indicates that the p is identified as a sentence <br>
1 -> Indicates that it is identified as a table title <br>
/< 0.5 -> Indicates that it is most likely not a table title. This category was majorly created to keep the table titles with the word Cont'd <br>
/> 0.5 -> Indicates that it is identified as a table title. This category might use the next ptag to get the complete table title <br>


In [155]:
def count_digits_in_string(word):
    digit_count = 0
    for a in word:
        if a.isdigit():
            digit_count = digit_count + 1
    return(digit_count)


count_digits_in_string("erio265")

3

In [169]:
def categorize_tables(list_titles):
    categories = []
    for title in list_titles: 
        table_string = title.replace('\n','').replace('\r','').replace('–',"").replace(":","").replace("-","").replace("(","")
        table_string = table_string.replace('.','')
        category = 0
        
        """
        splts = re.split('\d+[\.:]?\s+', table_string) #one period or none after the last digit followed by one or more whitespace
        splt = []
        for spl in splts:
            if len(spl) > 0:
                splt.append(spl)
        """
        title_words = re.split(" ", table_string)
        
        title_words_no_blanks = []
        for title_word in title_words:
            if len(title_word) > 2:
                title_words_no_blanks.append(title_word)
            elif len(title_word) > 0 and count_digits_in_string(title_word) > 0:
                title_words_no_blanks.append(title_word)
        
        category = 0
        """
        print(splt)
        if(len(splt) > 1) and len(splt[1]) > 0:
            #print(splt[1])
            if splt[1][0].isupper() or splt[1][0].isdigit():
                category = 1
          """    
        
        
        if len(title_words_no_blanks) < 3: 
            category = 0.75
            
        if 'cont' in table_string.lower():
            category = 0.35
            
        
        #category2 = 0
        if len(title_words_no_blanks) > 2:
            if(title_words_no_blanks[2][0].isupper() or title_words_no_blanks[2][0].isdigit()):
                category = 1
            else:
                category = 0
            if(title_words_no_blanks[1][-1]== ',') or (title_words_no_blanks[1][-1]== ']') or (title_words_no_blanks[1][-1]== ')'):
                category = 0
            if(title_words_no_blanks[2][:4].lower() == 'cont'):
                category = 0.35
            
        if len(title_words_no_blanks) == 3 :
            category = 0.5
            if(title_words_no_blanks[1][0].isdigit() and  title_words_no_blanks[1][0].isupper()):
                category = 0.65
            if(title_words_no_blanks[2][0].lower() == 'c'):
                category = 0.55
            if(title_words_no_blanks[2][:4].lower() == 'cont'):
                category = 0.35
            
        
        
        #print(title_words_no_blanks)
        categories.append(category)
        print("{} is {}. {} ".format(title, category, title_words_no_blanks))
            
    return(categories)

In [170]:
#performance check for the logic 
Tble = ["Table 5 of the As‐Built Report (page 20) reported the following for West Conifer Creek: ","table 1 (hello Nipun1", "Table 3 (continued) – List of Environmental Deficiencies", "Table 8 – Rough Fescue Plug Planting and Long-Term Monitoring Plots Observations (cont’d"]
categorize_tables(Tble)

Table 5 of the As‐Built Report (page 20) reported the following for West Conifer Creek:  is 0. ['Table', '5', 'the', 'As‐Built', 'Report', 'page', '20)', 'reported', 'the', 'following', 'for', 'West', 'Conifer', 'Creek'] 
table 1 (hello Nipun1 is 0. ['table', '1', 'hello', 'Nipun1'] 
Table 3 (continued) – List of Environmental Deficiencies is 0.35. ['Table', '3', 'continued)', 'List', 'Environmental', 'Deficiencies'] 
Table 8 – Rough Fescue Plug Planting and Long-Term Monitoring Plots Observations (cont’d is 1. ['Table', '8', 'Rough', 'Fescue', 'Plug', 'Planting', 'and', 'LongTerm', 'Monitoring', 'Plots', 'Observations', 'cont’d'] 


[0, 0, 0.35, 1]

In [171]:
categorize_tablesgorize_tablesgorize_tablesgories = []
categories = categorize_tables(table_title)

Figure is 0.75. ['Figure'] 
FIGURE 1REGIONAL LOCATION is 0.5. ['FIGURE', '1REGIONAL', 'LOCATION'] 
FIGURE 2LOCATION OF WATERCOURSE CROSSINGS is 1. ['FIGURE', '2LOCATION', 'WATERCOURSE', 'CROSSINGS'] 
TABLE 1   is 0.75. ['TABLE', '1'] 
TABLE 2   is 0.75. ['TABLE', '2'] 
TABLE 3   is 0.75. ['TABLE', '3'] 
TABLE 4   is 0.75. ['TABLE', '4'] 
TABLE 4  Cont'd  is 0.35. ['TABLE', '4', "Cont'd"] 
TABLE 4  Cont'd  is 0.35. ['TABLE', '4', "Cont'd"] 
TABLE 4  Cont'd  is 0.35. ['TABLE', '4', "Cont'd"] 
TABLE 4  Cont'd  is 0.35. ['TABLE', '4', "Cont'd"] 
TABLE 4  Cont'd  is 0.35. ['TABLE', '4', "Cont'd"] 
TABLE 4  Cont'd  is 0.35. ['TABLE', '4', "Cont'd"] 
TABLE 5   is 0.75. ['TABLE', '5'] 
TABLE 5  Cont’d  is 0.35. ['TABLE', '5', 'Cont’d'] 
TABLE 5  Cont’d  is 0.35. ['TABLE', '5', 'Cont’d'] 
TABLE 5  Cont’d  is 0.35. ['TABLE', '5', 'Cont’d'] 
TABLE 6   is 0.75. ['TABLE', '6'] 
TABLE 6  Cont’d  is 0.35. ['TABLE', '6', 'Cont’d'] 
TABLE 6  Cont’d  is 0.35. ['TABLE', '6', 'Cont’d'] 
TABLE 6  Cont’d  i

TABLE 3.3-3 Cont'd  is 0.35. ['TABLE', '333', "Cont'd"] 
TABLE 3.3-3 Cont'd  is 0.35. ['TABLE', '333', "Cont'd"] 
TABLE 3.3-3 Cont'd  is 0.35. ['TABLE', '333', "Cont'd"] 
TABLE 3.3-3 Cont'd  is 0.35. ['TABLE', '333', "Cont'd"] 
TABLE 3.3-3 Cont'd  is 0.35. ['TABLE', '333', "Cont'd"] 
TABLE 3.3-3 Cont'd  is 0.35. ['TABLE', '333', "Cont'd"] 
FIGURE 3.3-5SOCIO-ECONOMIC AND HUMANOCCUP ANCY  AND RESOURCE USE is 1. ['FIGURE', '335SOCIOECONOMIC', 'AND', 'HUMANOCCUP', 'ANCY', 'AND', 'RESOURCE', 'USE'] 
Figure 1.1 provides an overview of the location of the Project.  is 0. ['Figure', '11', 'provides', 'overview', 'the', 'location', 'the', 'Project'] 
FIGURE 1.1PROJECT OVERVIEW is 0.5. ['FIGURE', '11PROJECT', 'OVERVIEW'] 
TABLE 1.1   is 0.75. ['TABLE', '11'] 
FIGURE 3.1EDMONTON OBSERVATION LOCATIONS is 1. ['FIGURE', '31EDMONTON', 'OBSERVATION', 'LOCATIONS'] 
FIGURE 3.2BLACK PINES is 0.5. ['FIGURE', '32BLACK', 'PINES'] 
FIGURE 3.3SUMAS OBSERVATION LOCATIONS is 1. ['FIGURE', '33SUMAS', 'OBSERVATIO

TABLE 5.2-2   is 0.75. ['TABLE', '522'] 
TABLE 5.2-2  Cont'd  is 0.35. ['TABLE', '522', "Cont'd"] 
TABLE 5.2-3    is 0.75. ['TABLE', '523'] 
TABLE 5.2-3  Cont'd  is 0.35. ['TABLE', '523', "Cont'd"] 
TABLE 5.3-1   is 0.75. ['TABLE', '531'] 
TABLE 5.3-1  Cont'd  is 0.35. ['TABLE', '531', "Cont'd"] 
TABLE 5.3-2   is 0.75. ['TABLE', '532'] 
TABLE 5.3-2  Cont'd  is 0.35. ['TABLE', '532', "Cont'd"] 
TABLE 5.3-3   is 0.75. ['TABLE', '533'] 
TABLE 5.4.2-1   is 0.75. ['TABLE', '5421'] 
TABLE 5.4.2-1  Cont'd  is 0.35. ['TABLE', '5421', "Cont'd"] 
TABLE 5.4.2-1  Cont'd  is 0.35. ['TABLE', '5421', "Cont'd"] 
TABLE 5.4.3-1    is 0.75. ['TABLE', '5431'] 
TABLE 5.4.3-1  Cont'd  is 0.35. ['TABLE', '5431', "Cont'd"] 
TABLE 5.4.3-1  Cont'd  is 0.35. ['TABLE', '5431', "Cont'd"] 
TABLE 5.4.3-1  Cont'd  is 0.35. ['TABLE', '5431', "Cont'd"] 
TABLE 5.4.3-1  Cont'd  is 0.35. ['TABLE', '5431', "Cont'd"] 
TABLE 5.4.3-1  Cont'd  is 0.35. ['TABLE', '5431', "Cont'd"] 
TABLE 5.4.4-1   is 0.75. ['TABLE', '5441'] 
TA

TABLE 5.5-23   is 0.75. ['TABLE', '5523'] 
TABLE 5.5-24   is 0.75. ['TABLE', '5524'] 
TABLE 5.5-25   is 0.75. ['TABLE', '5525'] 
TABLE 5.5-26   is 0.75. ['TABLE', '5526'] 
TABLE 5.5-27   is 0.75. ['TABLE', '5527'] 
TABLE 5.5-28   is 0.75. ['TABLE', '5528'] 
TABLE 5.5-29   is 0.75. ['TABLE', '5529'] 
TABLE 5.5-30   is 0.75. ['TABLE', '5530'] 
TABLE 5.5-31   is 0.75. ['TABLE', '5531'] 
TABLE 5.5-32   is 0.75. ['TABLE', '5532'] 
TABLE 5.5-33   is 0.75. ['TABLE', '5533'] 
TABLE 5.5-34   is 0.75. ['TABLE', '5534'] 
TABLE 5.5-35   is 0.75. ['TABLE', '5535'] 
TABLE 5.5-36   is 0.75. ['TABLE', '5536'] 
TABLE 5.5-37   is 0.75. ['TABLE', '5537'] 
TABLE 5.5-38   is 0.75. ['TABLE', '5538'] 
TABLE 5.5-39   is 0.75. ['TABLE', '5539'] 
TABLE 5.5-40   is 0.75. ['TABLE', '5540'] 
TABLE 5.5-41   is 0.75. ['TABLE', '5541'] 
TABLE 5.5-42   is 0.75. ['TABLE', '5542'] 
TABLE 5.5-43   is 0.75. ['TABLE', '5543'] 
TABLE 5.5-44   is 0.75. ['TABLE', '5544'] 
TABLE 5.5-45   is 0.75. ['TABLE', '5545'] 
TABLE 5.5-4

TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.6   is 0.75. ['TABLE', '716'] 
TABLE 7.1.7   is 0.75. ['TABLE', '717'] 
TABLE 7.1.7   is 0.75. ['TABLE', '717'] 
TABLE 7.1.7   is 0.75. ['TABLE', '717'] 
TABLE 7.1.7   is 0.75. ['TABLE', '717'] 
TABLE 7.1.7   is 0.75. ['TABLE', '717'] 
TABLE 7.1.7   is 0.75. ['TABLE', '717'] 
TABLE 7.1.7   is 0.75. ['TABLE', '717'] 
TABLE 7.1.7   is 0.75. ['TABLE', '717'] 
TABLE 7.1.8   is

...

FIGURE NO. A-2Area is 0.75. ['FIGURE', 'A2Area'] 
Table A-2 Summary of Topsoil Conservation Measures  is 1. ['Table', 'A2', 'Summary', 'Topsoil', 'Conservation', 'Measures'] 
Table A-3 Summary of Mitigation Measures for Facility Construction is 1. ['Table', 'A3', 'Summary', 'Mitigation', 'Measures', 'for', 'Facility', 'Construction'] 
Table A-3 Summary of Mitigation Measures for Facility Construction (cont’d) is 1. ['Table', 'A3', 'Summary', 'Mitigation', 'Measures', 'for', 'Facility', 'Construction', 'cont’d)'] 
Table A-3 Summary of Mitigation Measures for Facility Construction (cont’d) is 1. ['Table', 'A3', 'Summary', 'Mitigation', 'Measures', 'for', 'Facility', 'Construction', 'cont’d)'] 
Table A-3 Summary of Mitigation Measures for Facility Construction (cont’d) is 1. ['Table', 'A3', 'Summary', 'Mitigation', 'Measures', 'for', 'Facility', 'Construction', 'cont’d)'] 
Table A1-1 Summary of Erosion and Sediment Control Measures is 1. ['Table', 'A11', 'Summary', 'Erosion', 'and', 'Sedi

Table 9-88 Summary of Residual Environmental Effects on Wildlife (cont’d) Mitigation measures: (cont’d) 14 Develop food and waste storage protocols to avoid attracting wildlife (e.g., bears) to construction camps and work areas. 15 Establish speed limits in high risk areas on project roads and the RoW; reduce speed in the presence of wildlife. 16 Reduce line-of-sight along the RoW. 17 Follow aircraft flight guidelines. 18 Prohibit project personnel from harassing, disturbing, harvesting and feeding wildlife at all work areas. 19 For sensitive wildlife periods, identify work windows in consultation with the appropriate wildlife management agencies, provincial and federal 20 Conduct pre-disturbance surveys to identify important wildlife habitat features. 21 Track and report all wildlife incidents. 22 Limit the length of the open trench to facilitate wildlife movement, and install fencing where hazards have been identified.. 23 Maintain trench breakers and gaps in windrows and raised pipe

Table 5.11‐1.  Acoustic Environment Filing Requirements 13  is 0.75. ['Table\xa0511‐1\xa0', 'Acoustic\xa0Environment\xa0Filing\xa0Requirements\xa013\xa0'] 
Table 5.12‐1.  Heritage Resources Filing Requirements 1  is 0.75. ['Table\xa0512‐1\xa0', 'Heritage\xa0Resources\xa0Filing\xa0Requirements\xa01\xa0'] 
Table 5.12‐2.  Target Areas for HRIA and Associated Previously Recorded Sites in Saskatchewan* 1  is 0.75. ['Table\xa0512‐2\xa0', 'Target\xa0Areas\xa0for\xa0HRIA\xa0and\xa0Associated\xa0Previously\xa0Recorded\xa0Sites\xa0in\xa0Saskatchewan*\xa01\xa0'] 
FIGURE 5.12-1 is 0.75. ['FIGURE', '5121'] 
FIGURE 5.12-2 is 0.75. ['FIGURE', '5122'] 
FIGURE 5.12-3 is 0.75. ['FIGURE', '5123'] 
FIGURE 5.12-4 is 0.75. ['FIGURE', '5124'] 
FIGURE 5.12-5 is 0.75. ['FIGURE', '5125'] 
FIGURE 5.12-6 is 0.75. ['FIGURE', '5126'] 
Table 6.1‐1.  Elements and Predicted Interaction with Project Components 14  is 0.75. ['Table\xa061‐1\xa0', 'Elements\xa0and\xa0Predicted\xa0Interaction\xa0with\xa0Project\xa0Componen

Table 5-6 Proposed Facility and Pipeline Developments within the Tanghe Creek Lateral Loop No. 2 (Cranberry Section) RSA (cont’d)  is 1. ['Table', '56', 'Proposed', 'Facility', 'and', 'Pipeline', 'Developments', 'within', 'the', 'Tanghe', 'Creek', 'Lateral', 'Loop', '2', 'Cranberry', 'Section)', 'RSA', 'cont’d)'] 
Table 5-7 Cumulative CAC Emissions Associated with the Tanghe Creek Lateral Loop No. 2 (Cranberry Section) RSA  is 1. ['Table', '57', 'Cumulative', 'CAC', 'Emissions', 'Associated', 'with', 'the', 'Tanghe', 'Creek', 'Lateral', 'Loop', '2', 'Cranberry', 'Section)', 'RSA'] 
Table 5-8 shows the total CAC emissions associated with existing, proposed and Project sources for all  is 0. ['Table', '58', 'shows', 'the', 'total', 'CAC', 'emissions', 'associated', 'with', 'existing,', 'proposed', 'and', 'Project', 'sources', 'for', 'all'] 
Table 5-8 Cumulative CAC Emissions Associated with the Project  is 1. ['Table', '58', 'Cumulative', 'CAC', 'Emissions', 'Associated', 'with', 'the', 

Table 18-8 Cumulative Alteration to Viewscapes in the Regional Study Area   is 1. ['Table', '188', 'Cumulative', 'Alteration', 'Viewscapes', 'the', 'Regional', 'Study', 'Area'] 
Table 18-9 presents the area available for timber harvest in the cumulative effects RSA. This area was conservatively estimated to include all lands within the RSA that have not been previously disturbed.   is 0. ['Table', '189', 'presents', 'the', 'area', 'available', 'for', 'timber', 'harvest', 'the', 'cumulative', 'effects', 'RSA', 'This', 'area', 'was', 'conservatively', 'estimated', 'include', 'all', 'lands', 'within', 'the', 'RSA', 'that', 'have', 'not', 'been', 'previously', 'disturbed'] 
Table 18-9 Cumulative Reduction of Land Base for Timber Harvest in the Regional Study Area  is 1. ['Table', '189', 'Cumulative', 'Reduction', 'Land', 'Base', 'for', 'Timber', 'Harvest', 'the', 'Regional', 'Study', 'Area'] 
Table 18-10 provides effects characterization and significance evaluation for the assessed cumulat

In [172]:
final_table_title = []
for i in range(len(categories)):
    if categories[i] > 0.49 and categories[i] < 1:
        final_table_title.append(table_title[i].strip() + " " + table_title_next[i].strip())
    else:
        final_table_title.append(table_title[i].strip())
len(final_table_title)

39989

In [173]:
for i in range(len(categories)):
    if categories[i] == 0.35:
        if(file_name[i]== file_name[i-1]):
            final_table_title[i] = final_table_title[i-1]
        

In [174]:
#file_name[:10]

In [175]:
df_table_names = pd.DataFrame({'file_name' : file_name, 
                               'page_number' : page_number, 
                               'table_title' : table_title, 
                               'table_title_next' : table_title_next, 
                               'final_table_title' : final_table_title,
                                'categories' : categories})
df_table_names.shape
df_table_names['DataID'] = df_table_names['file_name'].str.replace('\n', ' ').str.replace('F:/Environmental Baseline Data/Version 4 - Final/Pickles/', '').str.replace('.pkl', '').astype(int)
#df_table_names['DataID_pdf'] = df_table_names['file_name'].str.replace('\n', ' ').str.replace('F:/Environmental Baseline Data/Version 4 - Final/Pickles/', '').str.replace('.pkl', '.pdf')
df_table_names['table_title'] = df_table_names['table_title'].str.replace('\n', ' ')
df_table_names = df_table_names.drop('file_name', axis = 1)

df_table_names_project = df_table_names.merge(index2, on = 'DataID')
df_table_names_project.loc[df_table_names_project['table_title'].str.contains('FIGURE'), 'Category'] = 'Figure'
df_table_names_project.loc[df_table_names_project['table_title'].str.contains('TABLE'), 'Category'] = 'Table'
df_table_names_project.loc[df_table_names_project['table_title'].str.contains('Figure'), 'Category'] = 'Figure'
df_table_names_project.loc[df_table_names_project['table_title'].str.contains('Table'), 'Category'] = 'Table'
df_table_names_project.loc[df_table_names_project['table_title'].str.contains('IMAGE'), 'Category'] = 'Figure'
df_table_names_project.loc[df_table_names_project['table_title'].str.contains('Image'), 'Category'] = 'Figure'
df_table_names_project.loc[df_table_names_project['table_title'].str.contains('PHOTO'), 'Category'] = 'Figure'
df_table_names_project.loc[df_table_names_project['table_title'].str.contains('Photo'), 'Category'] = 'Figure'
df_table_names_project.head()

(39989, 6)

page_number                                table_title  \
0            5                                     Figure   
1            5                  FIGURE 1REGIONAL LOCATION   
2            6  FIGURE 2LOCATION OF WATERCOURSE CROSSINGS   
3            8                                  TABLE 1     
4            9                                  TABLE 2     

                                    table_title_next  \
0                                             1_ Re    
1  AQUATIC SUMMARY REPORT FOR THE PROPOSED NOVA G...   
2  AQUATIC SUMMARY REPORT FOR THE PROPOSED NOVA G...   
3  HYDROMETRIC DATA FROM DISCHARGE STATIONS  IN T...   
4  FISH SPECIES THAT MAY OCCUR IN THE UPPER PEACE...   

                                   final_table_title  categories   DataID  \
0                                       Figure 1_ Re        0.75  1059614   
1  FIGURE 1REGIONAL LOCATION AQUATIC SUMMARY REPO...        0.50  1059614   
2          FIGURE 2LOCATION OF WATERCOURSE CROSSINGS        1.00  1059614   
3  TABLE 1 HYDROMETRIC DATA FROM DISCHARGE STATIO...        0.75  1059614   
4  TABLE 2 FISH SPECIES THAT MAY OCCUR IN THE UPP...        0.75  1059614   

                                file_name  \
0  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   
1  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   
2  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   
3  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   
4  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   

                                    application_name  \
0  2013-11-08 Application for North Montney Proje...   
1  2013-11-08 Application for North Montney Proje...   
2  2013-11-08 Application for North Montney Proje...   
3  2013-11-08 Application for North Montney Proje...   
4  2013-11-08 Application for North Montney Proje...   

                                     esa_folder_link DocumentID  ...  \
0  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   
1  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   
2  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   
3  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   
4  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   

                                    Link to Decision Location_x    Component  \
0  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    
1  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    
2  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    
3  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    
4  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    

                         Component PDF Name Component Index table_count  \
0  Appendix G: TERA Aquatics Summary Report            15.0        56.0   
1  Appendix G: TERA Aquatics Summary Report            15.0        56.0   
2  Appendix G: TERA Aquatics Summary Report            15.0        56.0   
3  Appendix G: TERA Aquatics Summary Report            15.0        56.0   
4  Appendix G: TERA Aquatics Summary Report            15.0        56.0   

      short_name        Location_y Commodity Category  
0  North Montney  British Columbia       Gas   Figure  
1  North Montney  British Columbia       Gas   Figure  
2  North Montney  British Columbia       Gas   Figure  
3  North Montney  British Columbia       Gas    Table  
4  North Montney  British Columbia       Gas    Table  

[5 rows x 35 columns]

In [176]:
len(index2)
#len(set(file_name))
len(df_table_names_project)

1921

40171

In [177]:
df_table_names_project['Application title short'].nunique()
df_table_names_project.shape
df_table_names_project['table_title'] = df_table_names_project['table_title'].str.strip()

37

(40171, 35)

In [178]:
save_string = 'F:/Environmental Baseline Data/Version 4 - Final/Support files/Table titles raw data/final_table_titles8.csv'
df_table_names_project.to_csv(save_string, index = False, encoding='utf-8-sig')

In [179]:
df_table_names_project.head()

page_number                                table_title  \
0            5                                     Figure   
1            5                  FIGURE 1REGIONAL LOCATION   
2            6  FIGURE 2LOCATION OF WATERCOURSE CROSSINGS   
3            8                                    TABLE 1   
4            9                                    TABLE 2   

                                    table_title_next  \
0                                             1_ Re    
1  AQUATIC SUMMARY REPORT FOR THE PROPOSED NOVA G...   
2  AQUATIC SUMMARY REPORT FOR THE PROPOSED NOVA G...   
3  HYDROMETRIC DATA FROM DISCHARGE STATIONS  IN T...   
4  FISH SPECIES THAT MAY OCCUR IN THE UPPER PEACE...   

                                   final_table_title  categories   DataID  \
0                                       Figure 1_ Re        0.75  1059614   
1  FIGURE 1REGIONAL LOCATION AQUATIC SUMMARY REPO...        0.50  1059614   
2          FIGURE 2LOCATION OF WATERCOURSE CROSSINGS        1.00  1059614   
3  TABLE 1 HYDROMETRIC DATA FROM DISCHARGE STATIO...        0.75  1059614   
4  TABLE 2 FISH SPECIES THAT MAY OCCUR IN THE UPP...        0.75  1059614   

                                file_name  \
0  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   
1  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   
2  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   
3  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   
4  B2-16 ESA_Appendix_G_Part1of4 (A3Q6H2)   

                                    application_name  \
0  2013-11-08 Application for North Montney Proje...   
1  2013-11-08 Application for North Montney Proje...   
2  2013-11-08 Application for North Montney Proje...   
3  2013-11-08 Application for North Montney Proje...   
4  2013-11-08 Application for North Montney Proje...   

                                     esa_folder_link DocumentID  ...  \
0  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   
1  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   
2  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   
3  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   
4  https://apps.cer-rec.gc.ca/REGDOCS/Item/LoadRe...     A3Q6H2  ...   

                                    Link to Decision Location_x    Component  \
0  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    
1  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    
2  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    
3  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    
4  https://apps.cer-rec.gc.ca/REGDOCS/Item/View/3...        TBD  Appendix G    

                         Component PDF Name Component Index table_count  \
0  Appendix G: TERA Aquatics Summary Report            15.0        56.0   
1  Appendix G: TERA Aquatics Summary Report            15.0        56.0   
2  Appendix G: TERA Aquatics Summary Report            15.0        56.0   
3  Appendix G: TERA Aquatics Summary Report            15.0        56.0   
4  Appendix G: TERA Aquatics Summary Report            15.0        56.0   

      short_name        Location_y Commodity Category  
0  North Montney  British Columbia       Gas   Figure  
1  North Montney  British Columbia       Gas   Figure  
2  North Montney  British Columbia       Gas   Figure  
3  North Montney  British Columbia       Gas    Table  
4  North Montney  British Columbia       Gas    Table  

[5 rows x 35 columns]

In [180]:
a = " vibudh "
a = a.strip()
a
a[-1]
b = "s"
b[-1]

'vibudh'

'h'

's'